In [18]:
## 필요한 라이브러리 로딩
import pandas as pd
from datetime import datetime, timedelta
from pandas.api.types import CategoricalDtype
import plotly.graph_objects as go

## 1. covid19 원본 데이터 셋 로딩
## covid19 데이터 로딩(파일을 다운로드 받은 경우)
df_covid19 = pd.read_csv("D:/R/git/datavisualization/plotly/RnPy/owid-covid-data_221203.csv")

## covid19 데이터 로딩(온라인에서 바로 로딩할 경우)
##df_covid19 = pd.read_csv("https://covid.ourworldindata.org/data/owid-covid-data.csv")

## 2. 전체 데이터셋 중 최근 100일간의 데이터를 필터링한 df_covid19_100 생성
##df_covid19['date']를 datetime으로 변환
df_covid19['date'] = pd.to_datetime(df_covid19['date'], format="%Y-%m-%d")

## 대륙 데이터와 최종 데이터로부터 100일전 데이터 필터링
df_covid19_100 = df_covid19[(df_covid19['iso_code'].isin(['KOR', 'OWID_ASI', 'OWID_EUR', 'OWID_OCE', 'OWID_NAM', 'OWID_SAM', 'OWID_AFR'])) & (df_covid19['date'] >= (max(df_covid19['date']) - timedelta(days = 100)))]

##  대륙명을 한글로 변환
df_covid19_100.loc[df_covid19_100['location'] == 'South Korea', "location"] = '한국'
df_covid19_100.loc[df_covid19_100['location'] == 'Asia', "location"] = '아시아'
df_covid19_100.loc[df_covid19_100['location'] == 'Europe', "location"] = '유럽'
df_covid19_100.loc[df_covid19_100['location'] == 'Oceania', "location"] = '오세아니아'
df_covid19_100.loc[df_covid19_100['location'] == 'North America', "location"] = '북미'
df_covid19_100.loc[df_covid19_100['location'] == 'South America', "location"] = '남미'
df_covid19_100.loc[df_covid19_100['location'] == 'Africa', "location"] = '아프리카'

## 이산형 변수 설정
ord = CategoricalDtype(categories = ['한국', '아시아', '유럽', '북미', '남미', '아프리카', '오세아니아'], ordered = True)

df_covid19_100['location'] = df_covid19_100['location'].astype(ord)

## date로 정렬
df_covid19_100 = df_covid19_100.sort_values(by = 'date')

## 3. df_covid19_100을 한국과 각 대륙별열로 배치한 넓은 형태의 데이터프레임으로 변환
df_covid19_100_wide = df_covid19_100.loc[:,['date', 'location', 'new_cases', 'people_fully_vaccinated_per_hundred']].rename(columns={'new_cases':'확진자', 'people_fully_vaccinated_per_hundred':'백신접종완료자'})

df_covid19_100_wide = df_covid19_100_wide.pivot(index='date', columns='location', values=['확진자', '백신접종완료자']).sort_values(by = 'date')

df_covid19_100_wide.columns = ['확진자_한국', '확진자_아시아', '확진자_유럽', '확진자_북미', '확진자_남미', '확진자_아프리카','확진자_오세아니아',
                              '백신접종완료자_한국', '백신접종완료자_아시아', '백신접종완료자_유럽', '백신접종완료자_북미', '백신접종완료자_남미', '백신접종완료자_아프리카','백신접종완료자_오세아니아']
                              
## 4. covid19 데이터를 국가별로 요약한 df_covid19_stat 생성
df_covid19_stat = df_covid19.groupby(['iso_code', 'continent', 'location'], dropna=True).agg(
    인구수 = ('population', 'max'),
    전체사망자수 = ('new_deaths', 'sum'), 
    백신접종자완료자수 = ('people_fully_vaccinated', 'max'),
    인구백명당백신접종완료율 = ('people_fully_vaccinated_per_hundred', 'max'),
    인구백명당부스터접종자수 = ('total_boosters_per_hundred', 'max')
).reset_index()

df_covid19_stat['십만명당사망자수'] = round(df_covid19_stat['전체사망자수'] / df_covid19_stat['인구수'] *100000, 5)

df_covid19_stat['백신접종완료율'] = df_covid19_stat['백신접종자완료자수'] / df_covid19_stat['인구수']

## 여백 설정을 위한 변수 설정
margins_P = {'t' : 50, 'b' : 25, 'l' : 25, 'r' : 25}

C:\Anaconda3\lib\site-packages\pandas\core\indexing.py:1817: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

C:\Users\standard\AppData\Local\Temp/ipykernel_4220/3372635368.py:33: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



In [19]:
## python 코드
##  대학 학과 취업률 데이터 로딩

df_취업률 = pd.read_excel("d:/R/data/2020년 학과별 고등교육기관 취업통계.xlsx", 
                     ## '학과별' 시트의 데이터를 불러오는데,
                          sheet_name = '학과별',
                     ## 앞의 13행을 제외하고
                          skiprows=(13),
                     ## 첫번째 행은 열 이름으로 설정
                          header = 0)

## df_취업률에서 첫번째부터 9번째까지의 열과 '계'로 끝나는 열을 선택하여 다시 df_취업률에 저장
df_취업률 = pd.concat([df_취업률.iloc[:, 0:8], 
                    df_취업률.loc[:, df_취업률.columns.str.endswith('계')], 
                    df_취업률.loc[:, '입대자']], 
                   axis = 1
                   )

## df_취업률에서 졸업자가 500명 이하인 학과 중 25% 샘플링
df_취업률_500 = df_취업률.loc[(df_취업률['졸업자_계'] < 500)]

df_취업률_500 = df_취업률_500.iloc[range(0, len(df_취업률_500.index) , 4)]

df_취업률_500 = df_취업률_500.rename(columns = {'졸업자_계':'졸업자수', '취업률_계':'취업률', '취업자_합계_계':'취업자수'})

In [20]:
##  원본데이터 보존을 위해 데이터프레임 복사
total_deaths_5_nations_by_day = df_covid19.copy()
## 5개국 데이터로 전처리
total_deaths_5_nations_by_day = total_deaths_5_nations_by_day[(total_deaths_5_nations_by_day['iso_code'].isin(['KOR', 'USA', 'JPN', 'GBR', 'FRA']))].dropna(subset = ['total_deaths_per_million'])

##  라인 타입 설정을 위한 딕셔너리 정의
nations = {'France':'0', 'Japan':'1', 'South Korea':'2', 'United Kingdom':'3', 'United States':'4'}

##  plolty 초기화
fig = go.Figure()

##  국가별로 트레이스를 추가 
for location, group in total_deaths_5_nations_by_day.groupby('location'):
    fig.add_trace(go.Scatter(
        mode = 'lines', 
        x = group['date'], y = group['total_deaths_per_million'], 
        line = dict(dash = nations[location]), 
        name = location, connectgaps = True))

## layout의 제목, 축제목, 여백 속성 설정
fig.update_layout(title = dict(text = '코로나 19 사망자수 추세', x = 0.5), 
                  xaxis = dict(title = ''), 
                  yaxis = dict(title = '10만명당 사망자수 누계'))   

fig.show()

In [21]:
fig = go.Figure()
##  국가별로 그룹화하여 for 루프 실행
for location, group in total_deaths_5_nations_by_day.groupby('location'):
  ##  각국의 백만명당 사망자수 scatter 트레이스 생성
    fig.add_trace(go.Scatter(mode = 'lines', 
        x = group['date'], 
        y = group['total_deaths_per_million'], 
        line = dict(dash = nations[location]), 
        name = location, connectgaps = True, showlegend = False
    ))
    ##  각국의 마지막 날 옆에 국가명 scatter 트레이스 생성
    fig.add_trace(go.Scatter(
        mode = 'text',
        x = group.loc[group['date'] == group['date'].max(), 'date'], 
        y = group.loc[group['date'] == group['date'].max(), 'total_deaths_per_million'],
        text = group.loc[group['date'] == group['date'].max(), 'location'], 
        showlegend = False, 
        textposition = 'middle right'
    ))    

##  설날 표시를 위한 주석 추가
fig.add_annotation(
    x = '2022-02-01', 
    y = total_deaths_5_nations_by_day.loc[(total_deaths_5_nations_by_day['date'] == '2022-02-01') & (total_deaths_5_nations_by_day['iso_code'] == 'KOR'), 'total_deaths_per_million'].values[0],
    text = '설날', showarrow=True, arrowhead=1, arrowsize = 1.5
    )    

## layout의 제목, xaxis, yaxis 설정
fig.update_layout(title = dict(text = '코로나 19 사망자수 추세', x = 0.5), 
                  xaxis = dict(title = '', 
                               range = [total_deaths_5_nations_by_day['date'].min(),
                               total_deaths_5_nations_by_day['date'].max() + timedelta(days=150)]), 
                  yaxis = dict(title = '10만명당 사망자수 누계'))
                  
fig.show()


In [22]:
fig = go.Figure()

for location, group in total_deaths_5_nations_by_day.groupby('location'):
    fig.add_trace(go.Scatter(
        mode = 'lines', 
        x = group['date'], y = group['total_deaths_per_million'], 
        line = dict(dash = nations[location]), 
        name = location, connectgaps = True))

fig.update_layout(title = dict(text = '코로나 19 사망자수 추세', x = 0.5), 
                  xaxis = dict(title = '',
                    ## rangeslider  속성 설정
                    rangeslider = dict(visible = True)), 
                  yaxis = dict(title = '10만명당 사망자수 누계'))   
    
fig.show()

In [23]:
fig = go.Figure()

for location, group in total_deaths_5_nations_by_day.groupby('location'):
    fig.add_trace(go.Scatter(
        mode = 'lines', 
        x = group['date'], 
        y = group['total_deaths_per_million'], 
        line = dict(dash = nations[location]), 
        name = location,  connectgaps = True))

fig.update_layout(title = dict(text = '코로나 19 사망자수 추세', x = 0.5), 
                  xaxis = dict(title = '', 
                               ## rangeslider 속성 설정
                               rangeslider = dict(visible = True),
                               ## rangeselector 속성 설정
                               rangeselector=dict(
                                   ## rangeselector의 buttons 속성 설정
                                   buttons=list([
                                       dict(count=7, label='1 Week before', step='day', stepmode="backward"),
                                       dict(count=1, label='1 month before', step='month', stepmode="backward"),
                                       dict(count=6, label='6 months before', step="month", stepmode="backward"),
                                       dict(count=1, label='new years day', step="year", stepmode="todate"),
                                       dict(count=1, label='1 year before', step="year", stepmode="backward")
                                       ]))), 
                  yaxis = dict(title = '10만명당 사망자수 누계'))   
    
fig.show()

In [24]:
##  호버모드가 x인 시각화
fig = go.Figure()
for location, group in total_deaths_5_nations_by_day.groupby('location'):
    fig.add_trace(go.Scatter(
        mode = 'lines', 
        x = group['date'], 
        y = group['total_deaths_per_million'], 
        line = dict(dash = nations[location]), 
        name = location, connectgaps = True))
fig.update_layout(title = dict(text = '코로나 19 사망자수 추세', x = 0.5), 
                  xaxis = dict(title = ''), 
                  yaxis = dict(title = '10만명당 사망자수 누계'),
                  ## 호버 모드 설정
                  hovermode="x")       
fig.show()


In [25]:
##  호버모드가 y인 시각화
fig = go.Figure()
for location, group in total_deaths_5_nations_by_day.groupby('location'):
    fig.add_trace(go.Scatter(
        mode = 'lines', 
        x = group['date'], 
        y = group['total_deaths_per_million'], 
        line = dict(dash = nations[location]), 
        name = location, connectgaps = True))
fig.update_layout(title = dict(text = '코로나 19 사망자수 추세', x = 0.5), 
                  xaxis = dict(title = ''), 
                  yaxis = dict(title = '10만명당 사망자수 누계'),
                  ## 호버 모드 설정
                  hovermode="y")       
fig.show()

In [26]:
##  호버모드가 x unified인 시각화
fig = go.Figure()
for location, group in total_deaths_5_nations_by_day.groupby('location'):
    fig.add_trace(go.Scatter(
        mode = 'lines', 
        x = group['date'], 
        y = group['total_deaths_per_million'], 
        line = dict(dash = nations[location]), 
        name = location, connectgaps = True))
fig.update_layout(title = dict(text = '코로나 19 사망자수 추세', x = 0.5), 
                  xaxis = dict(title = ''), 
                  yaxis = dict(title = '10만명당 사망자수 누계'),
                  ## 호버 모드 설정
                  hovermode="x unified")       
fig.show()

In [27]:
##  호버모드가 y unified인 시각화
fig = go.Figure()
for location, group in total_deaths_5_nations_by_day.groupby('location'):
    fig.add_trace(go.Scatter(
        mode = 'lines', 
        x = group['date'], 
        y = group['total_deaths_per_million'], 
        line = dict(dash = nations[location]), 
        name = location, connectgaps = True))
fig.update_layout(title = dict(text = '코로나 19 사망자수 추세', x = 0.5), 
                  xaxis = dict(title = ''), 
                  yaxis = dict(title = '10만명당 사망자수 누계'),
                  ## 호버 모드 설정
                  hovermode="y unified")       
fig.show()

In [28]:
fig = go.Figure()

for location, group in total_deaths_5_nations_by_day.groupby('location'):
    fig.add_trace(go.Scatter(
        mode = 'lines', 
        x = group['date'], 
        y = group['total_deaths_per_million'], 
        line = dict(dash = nations[location]), 
        name = location, connectgaps = True))

fig.update_layout(title = dict(text = '코로나 19 사망자수 추세', x = 0.5), 
                  xaxis = dict(title = '', 
                      ##  X축의 spikemode 설정
                      spikemode = 'across'), 
                  yaxis = dict(title = '10만명당 사망자수 누계', 
                      ##  Y축의 spikemode 설정
                      spikemode = 'toaxis'), 
                  hovermode="x")   
    
fig.show()

In [29]:
fig = go.Figure()

for location, group in total_deaths_5_nations_by_day.groupby('location'):
    fig.add_trace(go.Scatter(
        mode = 'lines', 
        x = group['date'], 
        y = group['total_deaths_per_million'], 
        line = dict(dash = nations[location]), 
        name = location, connectgaps = True))

fig.update_layout(title = dict(text = '코로나 19 사망자수 추세', x = 0.5), 
                  xaxis = dict(title = '', spikemode = 'across',
                      ## X축 눈금 라벨 설정
                      tickformat = '%Y년 %m월',
                      ## X축 눈금 간격 설정
                      dtick = 'M3'), 
                  yaxis = dict(title = '10만명당 사망자수 누계', 
                      spikemode = 'toaxis'), 
                  hovermode="x")   
    
fig.show()

In [30]:
fig = go.Figure()
for location, group in total_deaths_5_nations_by_day.groupby('location'):
    fig.add_trace(go.Scatter(
        mode = 'lines', 
        x = group['date'], 
        y = group['total_deaths_per_million'], 
        line = dict(dash = nations[location]), 
        name = location, connectgaps = True))
        
fig.update_layout(title = dict(text = '코로나 19 사망자수 추세', x = 0.5), 
                  xaxis = dict(title = '', 
                      spikemode = 'across', tickformat = '%Y년 %m월',
                      ##  tickformatstops 설정
                      tickformatstops = (
                        ## 1000밀리초까지의 tickformat
                        dict(dtickrange=(None,1000), value="%H:%M:%S.%L 밀리초"),
                        ## 1초 ~ 1분까지의 tickformat
                        dict(dtickrange=(1000, 60000), value="%H:%M:%S 초"),
                        ## 1분 ~ 1시간까지의 tickformat
                        dict(dtickrange=(60000, 3600000), value="%H:%M 분"),
                        ## 1시간 ~ 1일까지의 tickformat
                        dict(dtickrange=(3600000, 86400000), value="%H:%M 시"),
                        ## 1일 ~ 1주까지의 tickformat
                        dict(dtickrange=(86400000, 604800000), value="%e. %b 일"),
                        ## 1주 ~ 1월까지의 tickformat
                        dict(dtickrange=(604800000, "M1"), value="%e. %b 주"),
                        ## 1월 ~ 1년까지의 tickformat
                        dict(dtickrange=("M1", "M12"), value="%b '%y 월"),
                        ## 1년 이상의 tickformat
                        dict(dtickrange=("M12",None), value="%Y 년")
                      )), 
                  yaxis = dict(title = '10만명당 사망자수 누계', 
                      spikemode = 'toaxis'), 
                  hovermode="x")   
    
fig.show()


In [2]:
import crypto
import sys
from Crypto.Cipher import AES  #Works
sys.modules['Crypto'] = crypto


ModuleNotFoundError: No module named 'Crypto'

In [1]:
import pandas_datareader as pdr
import yfinance as yf

yf.pdr_override()

stk_hist = pdr.get_data_yahoo('005930.KS',start='2000-01-01')
print(stk_hist)

ModuleNotFoundError: No module named 'Crypto'

In [7]:
import FinanceDataReader as fdr
from datetime import datetime, timedelta

start_day = datetime(2022, 10, 7)
end_day = start_day + timedelta(days = 100)

samsung_stock = fdr.DataReader('005930', start_day, end_day)
samsung_stock.head()

Open   High    Low  Close    Volume    Change
Date                                                      
2022-10-07  55900  56900  55200  56200  16886813 -0.001776
2022-10-11  54400  55700  54000  55400  21437877 -0.014235
2022-10-12  55700  57000  55200  55800  18408910  0.007220
2022-10-13  55400  56100  55200  55200  13784602 -0.010753
2022-10-14  56200  56500  55800  56300  12924326  0.019928

In [32]:
fig = go.Figure()
## cadlestick 트레이스 추가
fig.add_trace(go.Candlestick(
     x = samsung_stock.index,
     ## OHLC 데이터 설정
    open = samsung_stock['Open'], close = samsung_stock['Close'],
    high = samsung_stock['High'], low = samsung_stock['Low']
))

fig.update_layout(title = dict(text = "삼성전자 Candlestick Chart", x = 0.5))

fig.show()

In [33]:
fig = go.Figure()

fig.add_trace(go.Candlestick(
     x = samsung_stock.index,
    open = samsung_stock['Open'], close = samsung_stock['Close'],
    high = samsung_stock['High'], low = samsung_stock['Low'], 
    ##  상승시 선 색상 설정
    increasing = dict(line = dict(color = 'red')), 
    ##  하락시 선 색상 설정
    decreasing = dict(line = dict(color = 'blue'))))
    
fig.update_layout(title = dict(text = "삼성전자 Candlestick Chart", x = 0.5), 
         ## rangeslider는 안보이도록 설정
         xaxis = dict(rangeslider = dict(visible = False)))
         
fig.show()

In [34]:
##  서브 플롯을 위한 라이브러리 로딩
from plotly.subplots import make_subplots

##  서브플롯 설정
fig = make_subplots(rows = 2, cols = 1, row_heights=[0.7, 0.3], shared_xaxes = True)

fig.add_trace(go.Candlestick(
    x = samsung_stock.index,
    open = samsung_stock['Open'], close = samsung_stock['Close'],
    high = samsung_stock['High'], low = samsung_stock['Low'], 
    increasing = dict(line = dict(color = 'red')), 
    decreasing = dict(line = dict(color = 'blue'))), 
    row = 1, col = 1)

##  거래량 막대 그래프인 bar 트레이스 추가
fig.add_trace(go.Bar(
    x = samsung_stock.index,
    y = samsung_stock['Volume'], 
    marker = dict(color = 'gray')),
    row = 2, col =1)

##  서브플롯들의 Y축 제목 설정
fig.update_yaxes(title_text="주가", row=1, col=1)
fig.update_yaxes(title_text="거래량", row=2, col=1)

fig.update_layout(title = dict(text = "삼성전자 Candlestick Chart", x = 0.5),
                  xaxis = dict(rangeslider = dict(visible = False)), 
                  showlegend = False)

fig.show()

In [35]:
from plotly.subplots import make_subplots

fig = make_subplots(rows = 2, cols = 1, row_heights=[0.7, 0.3])

fig.add_trace(go.Candlestick(
    x = samsung_stock.index,
    open = samsung_stock['Open'], close = samsung_stock['Close'],
    high = samsung_stock['High'], low = samsung_stock['Low'], 
    increasing = dict(line = dict(color = 'red')), 
    decreasing = dict(line = dict(color = 'blue'))), 
    row = 1, col = 1)

fig.add_trace(go.Bar(
    x = samsung_stock.index,
    y = samsung_stock['Volume'], 
    marker = dict(color = 'gray'), 
    xaxis = 'x2'), 
    row = 2, col =1)

fig.update_xaxes(rangeslider = dict(visible = False), 
                 ##  rangebreaks 설정
                 rangebreaks = [
                   ## 주말 제거
                   dict(bounds=["sat", "mon"]),
                   ## 특정 공휴일 제거
                   dict(values=["2022-09-09", "2022-09-12", "2022-10-03", "2022-10-10"])
                   ],
                   row = 2, col = 1)

fig.update_yaxes(title_text="거래량", row=2, col=1)

fig.update_layout(xaxis = dict(rangeslider = dict(visible = False), 
                               ##  rangebreaks 설정
                               rangebreaks = [
                                   ## 주말 제거
                                   dict(bounds=["sat", "mon"]), 
                                   ## 특정 공휴일 제거
                                   dict(values=["2022-09-09", "2022-09-12", "2022-10-03", "2022-10-10"])                                    ]), 
                  yaxis = dict(title_text="주가"),
                  title = dict(text = "삼성전자 Candlestick Chart", x = 0.5),
                  showlegend = False)
                  
fig.show()

In [36]:
##  최근 100일간의 우리나라 코로나19 신규확진자 데이터 전처리
start_day = total_deaths_5_nations_by_day['date'].max() - timedelta(days=100)

total_deaths_5_nations_since_100day = total_deaths_5_nations_by_day.loc[(total_deaths_5_nations_by_day['iso_code'] =='KOR') & (total_deaths_5_nations_by_day['date'] > start_day)]

##  서브플롯 설정
fig = make_subplots(rows = 2, cols = 1, 
         subplot_titles=('주말이 포함된 확진자수','주말이 제거된 확진자수'))

##  주말이 포함된 scatter 트레이스 생성
fig.add_trace(go.Scatter(
    mode = 'lines', 
    x = total_deaths_5_nations_since_100day['date'], 
    y = total_deaths_5_nations_since_100day['new_cases'], 
    line = dict(color = 'darkblue'), 
    connectgaps = True), 
    row = 1, col = 1)

##   주말이 제거된 scatter 트레이스 생성
fig.add_trace(go.Scatter(
    mode = 'lines', 
    x = total_deaths_5_nations_since_100day['date'], 
    y = total_deaths_5_nations_since_100day['new_cases'], 
    line = dict(color = 'darkblue'), 
    connectgaps = True), 
    row = 2, col = 1) 

fig.update_xaxes(rangebreaks=[
                    dict(bounds=["sun", "tue"]), 
                    dict(values=['2022-03-02'])], 
                 row = 2, col = 1) 

fig.update_layout(title = dict(text = '우리나라의 코로나19 확진자수 추세', x = 0.5), 
                  hovermode = "x unified", 
                  showlegend = False)

fig.show()

In [37]:
##  5일, 20일, 40일 이동평균 산출
samsung_stock['M5'] = samsung_stock['Close'].rolling(5).mean()
samsung_stock['M20'] = samsung_stock['Close'].rolling(20).mean()
samsung_stock['M40'] = samsung_stock['Close'].rolling(40).mean() 
samsung_stock

from plotly.subplots import make_subplots

## 서브 플롯 설정
fig = make_subplots(rows = 2, cols = 1, row_heights=[0.7, 0.3])

##  candlestick 트레이스 생성
fig.add_trace(go.Candlestick(
    x = samsung_stock.index,
    open = samsung_stock['Open'], close = samsung_stock['Close'],
    high = samsung_stock['High'], low = samsung_stock['Low'], 
    increasing = dict(line = dict(color = 'red')), 
    decreasing = dict(line = dict(color = 'blue')), showlegend = False
    ), row = 1, col = 1)

##  5일 이동평균 scatter 트레이스 추가
fig.add_trace(go.Scatter(
    mode = 'lines',
    x = samsung_stock.index, y = samsung_stock['M5'], 
    name = '5일 이동평균', line = dict(dash = 'solid')), 
    row = 1, col = 1)

##  20일 이동평균 scatter 트레이스 추가
fig.add_trace(go.Scatter(
    mode = 'lines',
    x = samsung_stock.index, y = samsung_stock['M20'], 
    name = '20일 이동평균', line = dict(dash = 'dash')), 
    row = 1, col = 1)

##  40일 이동평균 scatter 트레이스 추가
fig.add_trace(go.Scatter(
    mode = 'lines',
    x = samsung_stock.index,  y = samsung_stock['M40'], 
    name = '40일 이동평균', line = dict(dash = 'dot')), 
    row = 1, col = 1)

##  거래량 bar 트레이스 추가
fig.add_trace(go.Bar(
    x = samsung_stock.index, y = samsung_stock['Volume'], 
    marker = dict(color = 'gray'), xaxis = 'x2', showlegend = False), 
    row = 2, col =1)

fig.update_xaxes(rangeslider = dict(visible = False), 
                 rangebreaks = [
                   dict(bounds=["sat", "mon"]), 
                   dict(values=["2022-09-09", "2022-09-12", "2022-10-03", "2022-10-10"])
                   ],
                 row = 2, col = 1)

fig.update_yaxes(title_text="거래량", row=2, col=1)

fig.update_layout(xaxis = dict(rangeslider = dict(visible = False), 
                               rangebreaks = [
                                   dict(bounds=["sat", "mon"]),
                                   dict(values=["2022-09-09", "2022-09-12", "2022-10-03", "2022-10-10"])
                                   ]), 
                  yaxis = dict(title_text="주가"),
                  title = dict(text = "삼성전자 Candlestick Chart", x = 0.5))

fig.show()

In [38]:
## 전일 종가 대비 등락가 전처리
samsung_stock['lag'] = samsung_stock['Close'] - samsung_stock['Close'].shift(1) 

fig = go.Figure()
## waterfall 트레이스 생성
fig.add_trace(go.Waterfall(
    name = "등락", orientation = "v",
    x = samsung_stock.index,
    y = samsung_stock['lag'],
    increasing = dict(marker = dict(color = 'red')), 
    decreasing = dict(marker = dict(color = 'blue'))))

fig.update_layout(xaxis = dict(rangeslider = dict(visible = False), 
                               rangebreaks = [
                                   dict(bounds=["sat", "mon"]),
                                   dict(values=["2022-09-09", "2022-09-12", "2022-10-03", "2022-10-10"])
                                   ]), 
                  yaxis = dict(title_text="주가 등락(원)"),
                  title = dict(text = "삼성전자 주가 Waterfall Chart", x = 0.5),
                  showlegend = False)

fig.show()

In [39]:
## funnel 트레이스를 위한 데이터 복사
df_취업률_funnel = df_취업률.copy()
##  funnel 트레이스를 위한 데이터 전처리
df_취업률_funnel['전체취업자'] = df_취업률_funnel[['취업자_교외취업자_계', '취업자_교내취업자_계']].sum(axis = 1) 

df_취업률_funnel = df_취업률_funnel[['전체취업자', '1차 유지취업자_계', '2차 유지취업자_계', '3차 유지취업자_계', '4차 유지취업자_계']].sum().reset_index()

df_취업률_funnel.columns = ['구분', '취업자수']

fig = go.Figure()

##  funnel 트레이스 생성
fig.add_trace(go.Funnel(
    x = df_취업률_funnel['취업자수'], 
    y = df_취업률_funnel['구분'],
    text = df_취업률_funnel['취업자수'], 
    textinfo = "text+percent initial"))

fig.update_layout(title = dict(text = '유지취업자 Funnel Chart', x = 0.5),
                  yaxis = dict(categoryorder = "total descending"))
                  
fig.show()

In [40]:
##  stack funnel 트레이스를 위한 데이터 복사
df_취업률_funnel_stack = df_취업률.copy()
## stack funnel 트레이스를 위한 데이터 전처리
df_취업률_funnel_stack['전체취업자'] = df_취업률_funnel_stack[['취업자_교외취업자_계', '취업자_교내취업자_계']].sum(axis = 1) 

df_취업률_funnel_stack = df_취업률_funnel_stack.groupby('과정구분')[['전체취업자', '1차 유지취업자_계', '2차 유지취업자_계', '3차 유지취업자_계', '4차 유지취업자_계']].agg(
    전체취업자 = ('전체취업자', sum),
    유지취업자_1차 = ('1차 유지취업자_계', sum),
    유지취업자_2차 = ('2차 유지취업자_계', sum),
    유지취업자_3차 = ('3차 유지취업자_계', sum),
    유지취업자_4차 = ('4차 유지취업자_계', sum))

df_취업률_funnel_stack = df_취업률_funnel_stack.transpose()

fig = go.Figure()

##  stack funnel 트레이스 생성
fig.add_trace(go.Funnel(
    x = df_취업률_funnel_stack['전문대학과정'], 
    y = df_취업률_funnel_stack.index,
    name = '전문대학과정',
    text = df_취업률_funnel_stack['전문대학과정'], 
    textinfo = "text+percent initial")
)
fig.add_trace(go.Funnel(
    x = df_취업률_funnel_stack['대학과정'], 
    y = df_취업률_funnel_stack.index,
    name = '대학과정',
    text = df_취업률_funnel_stack['대학과정'], 
    textinfo = "text+percent initial")
)

fig.update_layout(title = dict(text = '유지취업자 Funnel Chart', x = 0.5),
                  yaxis = dict(categoryorder = "total descending"))

fig.show()

In [41]:
##  funnelarea 트레이스를 위한 데이터 전처리
df_funnelarea = df_covid19_100_wide[['확진자_아시아', '확진자_유럽', '확진자_북미', '확진자_남미', '확진자_아프리카', '확진자_오세아니아']].sum().reset_index()

df_funnelarea.columns = ('대륙', '전체확진자수')

fig = go.Figure()

##  funnelarea 트레이스 생성
fig.add_trace(go.Funnelarea(
    text = df_funnelarea['대륙'], 
    values = df_funnelarea['전체확진자수'],
    textinfo = "text+value+percent"))

fig.update_layout(title = dict(text = '최근 100일간 대륙별 확진자수 Funnelarea 차트', x = 0.5))

fig.show()

In [42]:
##  과정구분 데이터에 따른 코드값을 반환하는 함수 생성
def cat_1(row):
    key = row['과정구분']
    value = {"전문대학과정" : 0, "대학과정": 1, "대학원과정" : 2}.get(key)
    return value

##  졸업구분 데이터에 따른 코드값을 반환하는 함수 생성
def cat_2(row):
    key = row['졸업구분']
    value = {"취업" : 3, "진학": 4, "취업불가" : 5, "외국인" : 6, "제외인정" : 7, "기타" : 8, "미상" : 9}.get(key)
    return value

##  sankey 트레이스를 위한 데이터 전처리
df_sankey = df_취업률.iloc[:, [2, 10, 19, 20, 21, 22, 23, 24]].groupby('과정구분').sum().reset_index()
df_sankey.columns = ('과정구분', '취업', '진학', '취업불가', '외국인', '제외인정', '기타', '미상')

##  데이터 형태를 변환
df_sankey = df_sankey.melt(id_vars = '과정구분', var_name = '졸업구분', value_name = '학생수').sort_values('과정구분')

##  과정구분_node와 졸업구분_node 값 설정
df_sankey['과정구분_node']= df_sankey.apply(cat_1, axis=1)
df_sankey['졸업구분_node']= df_sankey.apply(cat_2, axis=1)

In [43]:
import numpy as np

## 왼쪽 노드로 사용할 변량을 from에 저장
node_from = df_sankey['과정구분'].unique()

## 오른쪽 노드로 사용할 변량을 to에 저장
node_to = df_sankey['졸업구분'].unique()

## 전체 노드 배열 생성
node = np.concatenate((node_from, node_to))


In [44]:
fig = go.Figure()
fig.add_trace(go.Sankey(
    orientation = "h",
    node = dict(
      label = node,
      color = ['lightblue'] * 3 + ['darkblue'] * 7,
      pad = 15, thickness = 20,
      line = dict(color = "black", width = 0.5)),
    link = dict(
      source = df_sankey['과정구분_node'],
      target = df_sankey['졸업구분_node'],
      value =  df_sankey['학생수'])))

fig.update_layout(title = dict(text = '대학과정별 졸업자의 졸업 후 진로', x = 0.5))

fig.show()
